In [1]:
! %module magic necessary so that jupyter fortran kernel knows that 
! the code below is to be compiled as a module and not executable code.
%module: mod_initial
module mod_initial
    
    private
    public :: set_gaussian

contains
    
    pure subroutine set_gaussian(x, icenter, decay)
        real, intent(in out) :: x(:)
        integer, intent(in)  :: icenter
        real, intent(in)     :: decay
        
        integer :: i
    
        do concurrent(i = 1:size(x))
            x(i) = exp(-decay * (i - icenter)**2)
        end do
    end subroutine set_gaussian
    
end module mod_initial

[gfort kernel] module objects created successfully: mod_initial.o

In [3]:
! %module magic necessary so that jupyter fortran kernel knows that 
! the code below is to be compiled as a module and not executable code.
%module: mod_diff 
module mod_diff

    use iso_fortran_env, only: int32, real32
    implicit none
    
    private
    public :: diff_upwind, diff_centered
    
contains

    pure function diff_upwind(x) result(dx)
        real(real32), intent(in) :: x(:)
        real(real32)             :: dx(size(x))
        integer(int32)           :: im
        
        im       = size(x)
        dx(1)    = x(1) - x(im)
        dx(2:im) = x(2:im) - x(1:im - 1)
    end function diff_upwind
    
    pure function diff_centered(x) result(dx)
        real(real32), intent(in) :: x(:)
        real(real32)             :: dx(size(x))
        integer(int32)           :: im
        
        im         = size(x)
        dx(1)      = x(2) - x(im)
        dx(im)     = x(1) - x(im - 1)
        dx(2:im-1) = x(3:im) - x(1:im-2)
    end function diff_centered
    
end module mod_diff

[gfort kernel] module objects created successfully: mod_diff.o

In [7]:
%fcflags: mod_diff.o mod_initial.o
program tsunami

    use iso_fortran_env, only : int32, real32
    use mod_diff, only        : diff => diff_centered
    use mod_initial, only     : set_gaussian
    
    implicit none
    
    integer(int32) :: n
    
    integer(int32), parameter :: grid_size = 100
    integer(int32), parameter :: num_time_steps = 5000
    real(real32),   parameter :: dt = 0.02, dx = 1, g = 9.8
    real(real32),   parameter :: hmean = 10
    
    real(real32)              :: h(grid_size), u(grid_size)
    
    integer(int32), parameter :: icenter = 25
    real(real32), parameter   :: decay = 0.02
    
    logical :: file_exists
    
    open(9, file = 'data.txt')
    
    if (grid_size <= 0) stop 'grid_size must be > 0'
    if (dt <= 0) stop 'time step dt must be > 0'
    if (dx <= 0) stop 'grid spacing dx must be > 0'
    
    call set_gaussian(h, icenter, decay)
    u = 0
    
    print *, 0, h
    write (9, *) 0, h
    close(9)
    
    time_loop: do n = 1, num_time_steps
        
        u = u - (u * diff(u) + g * diff(h)) / dx * dt
        h = h - diff(u * (hmean + h)) / dx * dt
        
        print *, n, h
        
        inquire(file = 'data.txt', exist = file_exists)
        if (file_exists) then
            open(9, file = 'data.txt', status = 'old', position = 'append', action = 'write')
        else
            open(9, file = 'data.txt', status = "new", action = 'write')
        end if
        
        write (9, *) n, h

    end do time_loop
     
    close(9)
    
end program tsunami

           0   9.92950936E-06   2.54193492E-05   6.25215471E-05   1.47748404E-04   3.35462624E-04   7.31802545E-04   1.53381063E-03   3.08871618E-03   5.97602362E-03   1.11089963E-02   1.98410973E-02   3.40474583E-02   5.61347716E-02   8.89216289E-02  0.135335281      0.197898701      0.278037310      0.375311106      0.486752272      0.606530666      0.726149023      0.835270226      0.923116326      0.980198681       1.00000000      0.980198681      0.923116326      0.835270226      0.726149023      0.606530666      0.486752272      0.375311106      0.278037310      0.197898701      0.135335281       8.89216289E-02   5.61347716E-02   3.40474583E-02   1.98410973E-02   1.11089963E-02   5.97602362E-03   3.08871618E-03   1.53381063E-03   7.31802545E-04   3.35462624E-04   1.47748404E-04   6.25215471E-05   2.54193492E-05   9.92950936E-06   3.72665318E-06   1.34381298E-06   4.65571617E-07   1.54975410E-07   4.95640684E-08   1.52299791E-08   4.49635262E-09   1.27540822E-09   3.47589540E-10  

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



        2542  -6.43235072E-02  -6.04232177E-02  -5.51340096E-02  -4.96399812E-02  -4.43919152E-02  -3.92826833E-02  -3.36311497E-02  -2.67949831E-02  -1.89415067E-02  -1.08308643E-02  -3.44418595E-03   2.73611583E-03   8.34947918E-03   1.42839765E-02   2.08213292E-02   2.75432393E-02   3.33926640E-02   3.76283564E-02   4.03791480E-02   4.21011671E-02   4.32894118E-02   4.43687700E-02   4.55993414E-02   4.69473600E-02   4.76125069E-02   4.69477475E-02   4.55995835E-02   4.43689972E-02   4.32890207E-02   4.21011895E-02   4.03800979E-02   3.76296826E-02   3.33929174E-02   2.75431368E-02   2.08218992E-02   1.42844003E-02   8.34991410E-03   2.73522129E-03  -3.44383018E-03  -1.08308997E-02  -1.89420190E-02  -2.67947838E-02  -3.36300321E-02  -3.92816290E-02  -4.43912707E-02  -4.96408194E-02  -5.51333800E-02  -6.04233481E-02  -6.43234476E-02  -6.51331767E-02  -6.06646091E-02  -4.80141565E-02  -2.38099471E-02   1.64523907E-02   7.95946717E-02  0.173729166      0.304576576      0.467725575      

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



        4115  -6.47153780E-02  -6.42652512E-02  -5.92907667E-02  -4.13024202E-02   1.90952606E-03   8.87381732E-02  0.250983030      0.520251453      0.885412276       1.24316025       1.42293704       1.33266950       1.05093420      0.730694354      0.469509989      0.289353013      0.175601304      0.105302207       5.91578111E-02   2.55272686E-02  -5.43281843E-04  -1.88013762E-02  -2.81039756E-02  -3.12985331E-02  -3.19508314E-02  -3.12996991E-02  -2.81043947E-02  -1.88006386E-02  -5.42480382E-04   2.55254190E-02   5.91539890E-02  0.105297923      0.175594687      0.289341956      0.469491571      0.730667412       1.05090523       1.33264542       1.42293489       1.24317837      0.885441303      0.520278990      0.251001775       8.87499154E-02   1.91504695E-03  -4.13001925E-02  -5.92889860E-02  -6.42632395E-02  -6.47134110E-02  -6.35446757E-02  -6.01832755E-02  -5.60664311E-02  -5.37643209E-02  -5.39373383E-02  -5.83500676E-02  -6.68257847E-02  -7.52907246E-02  -8.23595822E-02  

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

